To do

- Clean notebook
- Add professor info
- Extend predictions to 6 years
- Use Lin Reg for predictions where arima fails

Imports

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
# import seaborn as sns
# from sklearn.preprocessing import LabelEncoder
# from sklearn.model_selection import train_test_split
# from sklearn.ensemble import RandomForestRegressor
# from sklearn.metrics import mean_squared_error
from statsmodels.tsa.arima.model import ARIMA
import numpy as np
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression

Read Data

In [2]:
df = pd.read_excel("../Datasets/data_clean3.xlsx")
df.head()

Trm Code  Year Academic Year  Month Start    Term Course Subject  \
0    202208  2022       2022-23            8    Fall           ACCT   
1    202105  2021       2021-22            5  Summer           ACCT   
2    201902  2019       2018-19            2  Spring           ACCT   
3    201408  2014       2014-15            8    Fall           ACCT   
4    201408  2014       2014-15            8    Fall           ACCT   

     College (imperfect mapping) Course Subject and Number  \
0   Scheller College of Business                 ACCT 2101   
1   Scheller College of Business                 ACCT 2101   
2   Scheller College of Business                 ACCT 2101   
3   Scheller College of Business                 ACCT 2101   
4   Scheller College of Business                 ACCT 2101   

  Primary Instructor Name Section  ...         B         C         D  \
0            Blunck, Ryan       E  ...  0.231884  0.144928       NaN   
1            Blunck, Ryan      ES  ...  0.060606  0.030303       NaN   
2            Blunck, Ryan       A  ...  0.235294  0.058824  0.044118   
3       Carlisle, Melissa     TSB  ...  0.413793  0.137931  0.068966   
4       Carlisle, Melissa     TSC  ...  0.371429  0.200000  0.085714   

          F         S   U         V   I         W  IJ  
0  0.072464       NaN NaN       NaN NaN  0.014493 NaN  
1  0.060606       NaN NaN  0.030303 NaN  0.030303 NaN  
2  0.014706  0.014706 NaN       NaN NaN  0.044118 NaN  
3       NaN       NaN NaN       NaN NaN  0.172414 NaN  
4  0.028571       NaN NaN  0.028571 NaN  0.085714 NaN  

[5 rows x 22 columns]

### Devanshu's Code - Start

Create New Dataframe

In [3]:
# list of all courses
courses_list = df["Course Subject and Number"].unique().tolist()

cols = ['2014_Spring', '2014_Summer', '2014_fall', '2015_Spring', '2015_Summer', '2015_fall', '2016_Spring', '2016_Summer', '2016_fall', 
        '2017_Spring', '2017_Summer', '2017_fall', '2018_Spring', '2018_Summer', '2018_fall', '2019_Spring', '2019_Summer', '2019_fall', 
        '2020_Spring', '2020_Summer', '2020_fall', '2021_Spring', '2021_Summer', '2021_fall', '2022_Spring', '2022_Summer', '2022_fall', '2023_Spring', '2023_Summer']

# create an empty dataframe to store courses' average grades over time from 2014 spring to 2023 summer
empty_df = pd.DataFrame(columns=cols)


# change Fall to fall (so values sort as Spring Summer fall)
change_fall = df.copy()
change_fall = change_fall.replace({'Term': 'Fall'}, {'Term': 'fall'})

# populate the empty_df
for course in courses_list:

#     # get only that course
#     course_df = change_fall[change_fall["Course Subject and Number"] == course]


#     # group by semester
#     new_df = course_df.groupby(["Year", "Term"]).mean().drop(columns=['Trm Code', 'Month Start', 'A', 'B', 'C', 'D', 'F', 'S', 'U', 'V', 'I', 'W', 'IJ'])

#     # unnecessary but good for debugging
#     new_df = new_df.reset_index(drop=False)
#     new_df['time'] = new_df['Year'].astype(str) + "_" + new_df['Term']
#     # print(new_df['time'])

#     # add to dataframe
#     new_df = new_df.set_index('time')
#     new_df = new_df.drop(columns=['Year', 'Term'])
#     new_df = new_df.rename(columns={'Average Grade': course})
#     new_df = new_df.transpose()
#     new_df.columns.name = ''

#     empty_df = pd.concat([empty_df, new_df])

        # Get only that course
    course_df = change_fall[change_fall["Course Subject and Number"] == course]

    # Convert relevant columns to numeric
    numeric_cols = ['Average Grade']  # Add other columns if needed
    course_df[numeric_cols] = course_df[numeric_cols].apply(pd.to_numeric, errors='coerce')

    # Group by semester and calculate the mean
    new_df = course_df.groupby(["Year", "Term"])[numeric_cols].mean().reset_index()

    # Create a 'time' column for indexing
    new_df['time'] = new_df['Year'].astype(str) + "_" + new_df['Term']

    # Add to the dataframe
    new_df = new_df.set_index('time')
    new_df = new_df.drop(columns=['Year', 'Term'])
    new_df = new_df.rename(columns={'Average Grade': course})
    new_df = new_df.transpose()
    new_df.columns.name = ''

    empty_df = pd.concat([empty_df, new_df])


/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/449484121.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  course_df[numeric_cols] = course_df[numeric_cols].apply(pd.to_numeric, errors='coerce')
/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/449484121.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  course_df[numeric_cols] = course_df[numeric_cols].apply(pd.to_numeric, errors='coerce')
/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/449484121.py:45

In [4]:
empty_df.head()

2014_Spring  2014_Summer  2014_fall  2015_Spring  2015_Summer  \
ACCT 2101     3.136000         3.29   3.038000     3.210000         3.21   
ACCT 2102     2.770000         3.27   3.120000     3.150000         3.55   
AE 1350       3.336667          NaN        NaN          NaN          NaN   
AE 1355       4.000000          NaN   3.956667     3.900000          NaN   
AE 1601            NaN          NaN   3.596667     3.746667          NaN   

           2015_fall  2016_Spring  2016_Summer  2016_fall  2017_Spring  ...  \
ACCT 2101   2.998000     3.086000         3.00      3.216     3.136000  ...   
ACCT 2102   3.290000     3.156667         3.11      3.160     3.226667  ...   
AE 1350          NaN          NaN          NaN        NaN          NaN  ...   
AE 1355     4.000000     4.000000          NaN      3.955     4.000000  ...   
AE 1601     3.626667     3.783333          NaN      3.900     3.733333  ...   

           2020_Summer  2020_fall  2021_Spring  2021_Summer  2021_fall  \
ACCT 2101         3.69   3.452500     3.036000         3.61   3.175000   
ACCT 2102         2.86   3.666667     3.566667         3.08   3.056667   
AE 1350            NaN        NaN          NaN          NaN        NaN   
AE 1355            NaN   4.000000     4.000000          NaN   4.000000   
AE 1601           4.00   3.826667     3.750000          NaN   3.863333   

           2022_Spring  2022_Summer  2022_fall  2023_Spring  2023_Summer  
ACCT 2101     2.832500         3.82   3.176000       3.2275         3.00  
ACCT 2102     3.673333          NaN   3.383333       3.5600         3.33  
AE 1350            NaN          NaN        NaN          NaN          NaN  
AE 1355       4.000000          NaN   4.000000       4.0000          NaN  
AE 1601       3.820000          NaN   3.930000       3.9000          NaN  

[5 rows x 29 columns]

 Rename columns in order to make time series analysis easier

In [5]:
testy_df = empty_df.rename(columns={'2014_Spring': 1, '2014_Summer': 2, '2014_fall': 3, '2015_Spring': 4, '2015_Summer': 5, '2015_fall': 6, '2016_Spring': 7, '2016_Summer': 8,
                                    '2016_fall': 9, '2017_Spring': 10, '2017_Summer': 11, '2017_fall': 12, '2018_Spring': 13, '2018_Summer': 14, '2018_fall': 15, '2019_Spring': 16, 
                                    '2019_Summer': 17, '2019_fall': 18, '2020_Spring': 19, '2020_Summer': 20, '2020_fall': 21, '2021_Spring': 22, '2021_Summer': 23, '2021_fall': 24, 
                                    '2022_Spring': 25, '2022_Summer': 26, '2022_fall': 27, '2023_Spring': 28, '2023_Summer': 29})

# start by forecasting for courses with no NaN values
df_1 = testy_df.dropna()
df_2 = testy_df.copy()


Separate into seasons

In [6]:
df_spring = df_2.iloc[:,0::3]
df_summer = df_2.iloc[:,1::3]
df_fall = df_2.iloc[:, 2::3] 

### Devanshu's Code - End

## Impute Nan Values

Method:
- Up to the first non-nan value set them all equal to the first non-nan value you see on the right
- After that use linear interpolation between non-nan value to the left and right
- If no non-nan value to the right then just use the last non-nan value you see throughout

First drop rows if they are all nans

In [7]:
print(len(df_spring), len(df_summer), len(df_fall))

5092 5092 5092


In [8]:
df_spring = df_spring.dropna(how="all")
df_summer = df_summer.dropna(how="all")
df_fall = df_fall.dropna(how="all")

In [9]:
print(len(df_spring), len(df_summer), len(df_fall))

3429 1409 3157


Function to fill nans

In [10]:
def fill_nans(df):
    # Forward fill NaNs at the start of each row
    df_filled = df.apply(lambda x: x.ffill().bfill() if x.first_valid_index() is None else x, axis=1)
    
    # Apply linear interpolation for remaining NaNs
    df_filled = df_filled.interpolate(method='linear', axis=1, limit_direction='both')

    return df_filled

In [11]:
df_spring = fill_nans(df_spring)
df_summer = fill_nans(df_summer)
df_fall = fill_nans(df_fall)

In [12]:
print(df_spring.isna().any().sum(), df_summer.isna().any().sum(),df_fall.isna().any().sum())

0 0 0


Backup this for now

In [13]:
df_spring_backup = df_spring.copy()
df_summer_backup = df_summer.copy()
df_fall_backup = df_fall.copy()

In [73]:
df_spring_backup.index.nunique(), df_summer_backup.index.nunique(), df_fall_backup.index.nunique()

(3429, 1409, 3157)

In [14]:
# df_spring = df_spring_backup.copy()



Define parameters to use
- Got these after evaluating Arima models with Gridsearch

In [15]:
best_params_per_semester = {0: (2, 1, 1)
                            , 1: (2, 1, 1),
                            2: (2, 1, 1)}

## Make new predictions for the next 6 years

In [16]:
df_spring.index.nunique(), df_summer.index.nunique(), df_fall.index.nunique()

(3429, 1409, 3157)

### Linearly extrapolate values first

In [17]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures

Store original column names just in case

In [77]:
original_columns = [df_spring.columns, df_summer.columns, df_fall.columns]

In [23]:
df_spring.columns = [1,2,3,4,5,6,7,8,9,10]
df_summer.columns = [1,2,3,4,5,6,7,8,9,10]
df_fall.columns = [1,2,3,4,5,6,7,8,9]

In [98]:
# df_spring['Course'] = df_spring.index

In [19]:
dfs = [df_spring, df_summer, df_fall]

Create course list

In [20]:
spring_courses = df_spring.index.to_list()
summer_courses = df_summer.index.to_list()
fall_courses = df_fall.index.to_list()
courses = [spring_courses, summer_courses, fall_courses]

Making predictions

In [27]:
df_fall

1         2         3         4         5         6  \
ACCT 2101  3.038000  2.998000  3.216000  3.246000  3.474000  3.420000   
ACCT 2102  3.120000  3.290000  3.160000  2.926667  3.086667  3.416667   
AE 1355    3.956667  4.000000  3.955000  4.000000  4.000000  4.000000   
AE 1601    3.596667  3.626667  3.900000  3.906667  3.746667  3.846667   
AE 2010    2.835000  2.835000  2.693333  2.803333  3.170000  2.956667   
...             ...       ...       ...       ...       ...       ...   
VIP 6602   3.875000  3.875000  3.875000  3.875000  3.875000  3.875000   
VIP 6603   4.000000  4.000000  4.000000  4.000000  4.000000  3.863636   
WOLO 1801  3.800000  3.800000  3.800000  3.800000  3.800000  3.800000   
WOLO 1811  3.880000  3.880000  3.880000  3.880000  3.880000  3.880000   
WOLO 3420  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000   

                  7         8         9  
ACCT 2101  3.452500  3.175000  3.176000  
ACCT 2102  3.666667  3.056667  3.383333  
AE 1355    4.000000  4.000000  4.000000  
AE 1601    3.826667  3.863333  3.930000  
AE 2010    3.020000  3.096667  3.360000  
...             ...       ...       ...  
VIP 6602   3.875000  4.000000  4.000000  
VIP 6603   3.954545  3.891667  3.895833  
WOLO 1801  3.800000  3.800000  3.800000  
WOLO 1811  3.880000  3.880000  3.880000  
WOLO 3420  4.000000  4.000000  4.000000  

[3157 rows x 9 columns]

In [30]:
mse_per_semester = [0,0,0]
valid_course_nums = [0,0,0]
prediction_indices = [11,11,10]

# initialize prediction dataframes
time_steps = [10,11,12,13,14,15,16]
df_spring_predictions = pd.DataFrame(columns=time_steps[1:])
df_summer_predictions = pd.DataFrame(columns=time_steps[1:])
df_fdf = pd.DataFrame(columns=time_steps[:-1])
prediction_dfs = [df_spring_predictions, df_summer_predictions, df_fdf]


# Loop through each semester
for semester in range(3):
    df = dfs[semester]
    course_list = courses[semester]
    prediction_index = prediction_indices[semester] 

    # Set params
    params = best_params_per_semester[semester]
    p = params[0]
    d = params[1]
    q = params[2]


    total_mse = 0

    print("Now at semester ", semester)

    total_train_mse = 0

    valid_courses = 0

    # Iterate over each course
    for course_name in course_list:
        try:
            # Extract the training and testing series for this course
            train_row = df.loc[course_name].tolist()
            
            # Fit the ARIMA model to this course's training data
            model = ARIMA(train_row, order=(p, d, q)).fit()

            # Predict 
            train_pred = model.predict()
            train_pred[0] = train_row[0] # fill in first value
            
            # Predict next step
            prediction = model.predict(start = prediction_index, end = prediction_index + 5) # no need for start end

        except Exception as e:
            continue


        
        # Append predictions to the corresponding semester DataFrame
        prediction_dfs[semester].loc[course_name] = prediction

        # Compute and add MSE
        train_mse = mean_squared_error(train_row, model.predict(start=0, end=len(train_row)-1))
        total_mse += train_mse
        valid_courses += 1

    # Calculate combined MSE and update the best parameters if necessary
    if valid_courses > 0:
        mse_per_semester[semester] = total_mse / valid_courses
    
    valid_course_nums[semester] = valid_courses


Now at semester  0


/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  

Now at semester  1


/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  

Now at semester  2


/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/feyzjan/miniconda3/envs/data_analysis/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zero

In [31]:
print(valid_course_nums)

[3426, 1409, 3157]


In [40]:
df_spring_predictions = prediction_dfs[0]
df_summer_predictions = prediction_dfs[1]
df_fdf = prediction_dfs[2]


### Merge this to the original dataframes

In [43]:
df_spring = df_spring.merge(df_spring_predictions, how='left', left_index=True, right_index=True)
df_summer = df_summer.merge(df_summer_predictions, how='left', left_index=True, right_index=True)
df_fall = df_fall.merge(df_fdf, how='left', left_index=True, right_index=True)

Check for NANs

In [48]:
df_spring.isna().any().sum(), df_summer.isna().any().sum(), df_fall.isna().any().sum()

(6, 0, 0)

In [49]:
df_spring[df_spring.isna().any(axis=1)]

1     2     3     4     5     6     7     8     9     10  11  12  \
AE 3521    2.87  3.38  2.74  2.96  2.96  2.96  2.96  2.96  2.96  2.96 NaN NaN   
ECE 4753   4.00  3.50  4.00  3.80  3.80  3.80  3.80  3.80  3.80  3.80 NaN NaN   
ECON 7112  3.75  4.00  3.67  3.71  3.71  3.71  3.71  3.71  3.71  3.71 NaN NaN   

           13  14  15  16  
AE 3521   NaN NaN NaN NaN  
ECE 4753  NaN NaN NaN NaN  
ECON 7112 NaN NaN NaN NaN

In [50]:
# fill nans
df_spring = fill_nans(df_spring)

Rename columns

In [59]:
df_fall.columns

Int64Index([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15], dtype='int64')

In [61]:
df_spring.columns = [1,4,7,10,13,16,19,22,25,28,31,34,37,40,43,46]
df_summer.columns = [2,5,8,11,14,17,20,23,26,29,32,35,38,41,44,47]
df_fall.columns =   [3,6,9,12,15,18,21,24,27,30,33,36,39,42,45]

Combine all into single df

In [195]:
df = df_spring.merge(df_summer, how='outer', left_index=True, right_index=True)
df = df.merge(df_fall, how='outer', left_index=True, right_index=True)

In [196]:
df.index.nunique()

4579

In [197]:
empty_df.isna().any().sum()

29

Sort columns

In [198]:
cols_sorted = sorted(df.columns)

df = df[cols_sorted]

In [199]:
df.head()

1     2         3         4     5         6         7     8   \
ACCT 2101  3.136000  3.29  3.038000  3.210000  3.21  2.998000  3.086000  3.00   
ACCT 2102  2.770000  3.27  3.120000  3.150000  3.55  3.290000  3.156667  3.11   
AE 1350    3.336667   NaN       NaN  3.336667   NaN       NaN  3.336667   NaN   
AE 1355    4.000000   NaN  3.956667  3.900000   NaN  4.000000  4.000000   NaN   
AE 1601    3.746667  4.00  3.596667  3.746667  4.00  3.626667  3.783333  4.00   

              9         10  ...        38        39        40        41  \
ACCT 2101  3.216  3.136000  ...  3.205621  2.816882  3.072566  3.234039   
ACCT 2102  3.160  3.226667  ...  3.227541  3.359264  3.509813  3.229542   
AE 1350      NaN  3.336667  ...       NaN       NaN  3.336667       NaN   
AE 1355    3.955  4.000000  ...       NaN  4.000000  4.000000       NaN   
AE 1601    3.900  3.733333  ...  4.000000  3.885728  3.843286  4.000000   

                 42        43        44        45        46        47  
ACCT 2101  2.908065  2.942821  3.218919  2.783447  3.067042  3.226656  
ACCT 2102  3.342054  3.504470  3.228847  3.342403  3.507211  3.228301  
AE 1350         NaN  3.336667       NaN       NaN  3.336667       NaN  
AE 1355    4.000000  4.000000       NaN  4.000000  4.000000       NaN  
AE 1601    3.887007  3.842477  4.000000  3.883027  3.838174  4.000000  

[5 rows x 47 columns]

Add course as separate column to df

In [200]:
df['Course'] = df.index
df.reset_index(drop=True, inplace=True)


In [201]:
df.head()

1     2         3         4     5         6         7     8      9  \
0  3.136000  3.29  3.038000  3.210000  3.21  2.998000  3.086000  3.00  3.216   
1  2.770000  3.27  3.120000  3.150000  3.55  3.290000  3.156667  3.11  3.160   
2  3.336667   NaN       NaN  3.336667   NaN       NaN  3.336667   NaN    NaN   
3  4.000000   NaN  3.956667  3.900000   NaN  4.000000  4.000000   NaN  3.955   
4  3.746667  4.00  3.596667  3.746667  4.00  3.626667  3.783333  4.00  3.900   

         10  ...        39        40        41        42        43        44  \
0  3.136000  ...  2.816882  3.072566  3.234039  2.908065  2.942821  3.218919   
1  3.226667  ...  3.359264  3.509813  3.229542  3.342054  3.504470  3.228847   
2  3.336667  ...       NaN  3.336667       NaN       NaN  3.336667       NaN   
3  4.000000  ...  4.000000  4.000000       NaN  4.000000  4.000000       NaN   
4  3.733333  ...  3.885728  3.843286  4.000000  3.887007  3.842477  4.000000   

         45        46        47     Course  
0  2.783447  3.067042  3.226656  ACCT 2101  
1  3.342403  3.507211  3.228301  ACCT 2102  
2       NaN  3.336667       NaN    AE 1350  
3  4.000000  4.000000       NaN    AE 1355  
4  3.883027  3.838174  4.000000    AE 1601  

[5 rows x 48 columns]

### Match with professors

In [202]:
df_instructor = pd.read_excel('../Datasets/GPA_by_prof_course_college_clean.xlsx')
df_instructor.head()

College (imperfect mapping) Course Subject and Number  \
0        College of Computing                   CS 1100   
1        College of Computing                   CS 1100   
2        College of Computing                   CS 1100   
3        College of Computing                   CS 1100   
4        College of Computing                   CS 1100   

  Primary Instructor Name  201408  201401  201405  201508  201501  201505  \
0             Peace, Troy     NaN     NaN     NaN     NaN     NaN     NaN   
1    Raczynski, Katharine     NaN     NaN     NaN     NaN     NaN     NaN   
2            Rose, Ashley     NaN     NaN     NaN     NaN     NaN     NaN   
3      Stallworth, Cedric     NaN     NaN     NaN     NaN     NaN     NaN   
4        Steele, Christen     NaN     NaN     NaN     NaN     NaN     NaN   

   201608  ...  202001  202005  202108  202101  202105  202208  202201  \
0     NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1     NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2     NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

   202205  202308  202301  
0     NaN     NaN     NaN  
1     NaN     NaN     NaN  
2     NaN     NaN     NaN  
3     NaN     NaN     NaN  
4     NaN     NaN     NaN  

[5 rows x 32 columns]

Sort columns

In [203]:
sorted_cols = sorted(df_instructor.columns)
df_instructor = df_instructor[sorted_cols]

Separate instructor dataframe into 3 after renaming

In [204]:
df_instructor.columns = [1,2,3,4,5,6, 7,8,9, 10,11,12, 13,14,15, 16,17,18, 19,20,21, 22,23,24, 25,26,27, 28,29, 'College', 'Course', 'Instructor']

In [205]:
df_instructor.drop(columns=['College'], inplace=True)

In [206]:
df_instructor_spring = df_instructor[['Course', 'Instructor', 1, 4, 7, 10, 13, 16, 19, 22, 25, 28]]
df_instructor_summer = df_instructor[['Course', 'Instructor', 2, 5, 8, 11, 14, 17, 20, 23, 26, 29]]
df_instructor_fall = df_instructor[['Course', 'Instructor', 3, 6, 9, 12, 15, 18, 21, 24, 27]]

df_instructor_spring.dropna(subset=[1, 4, 7, 10, 13, 16, 19, 22, 25, 28], how='all', inplace=True)
df_instructor_summer.dropna(subset=[2, 5, 8, 11, 14, 17, 20, 23, 26, 29], how='all', inplace=True)
df_instructor_fall.dropna(subset=[3, 6, 9, 12, 15, 18, 21, 24, 27], how='all', inplace=True)

/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/1753249861.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_instructor_spring.dropna(subset=[1, 4, 7, 10, 13, 16, 19, 22, 25, 28], how='all', inplace=True)
/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/1753249861.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_instructor_summer.dropna(subset=[2, 5, 8, 11, 14, 17, 20, 23, 26, 29], how='all', inplace=True)
/var/folders/n8/cpfk46ss313d61dgywbkx80m0000gn/T/ipykernel_97778/1753249861.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

Print unique course numbers to check

In [207]:
df_instructor_spring['Course'].nunique(), df_instructor_summer['Course'].nunique(), df_instructor_fall['Course'].nunique()

(1409, 3693, 3303)

Group by each course, keep the instructor that appears at the latest column

In [208]:
last_instructors = {}

dfs = [df_instructor_spring, df_instructor_summer, df_instructor_fall]
result_dfs = [pd.DataFrame, pd.DataFrame, pd.DataFrame]


for i in range(len(dfs)):
    temp_df = dfs[i].copy()
    last_instructors = {}
    # Iterate over each unique course
    for course in temp_df['Course'].unique():
        course_df = temp_df[temp_df['Course'] == course]  # Filter rows for the current course
        
        # Iterate over columns in reverse order, skipping 'Course' and 'Instructor'
        for col in reversed(temp_df.columns.drop(['Course', 'Instructor'])):
            # Drop NaN values and get the last instructor
            last_instructor = course_df.dropna(subset=[col])['Instructor'].values[-1] if not course_df[course_df[col].notna()].empty else None
            if last_instructor:
                last_instructors[course] = last_instructor
                break

    # Convert the result to a DataFrame
    result_dfs[i] = pd.DataFrame(list(last_instructors.items()), columns=['Course', 'Instructor'])

Merge

In [209]:
result_dfs[0].columns = ['Course', 'Instructor_Spring']
result_dfs[1].columns = ['Course', 'Instructor_Summer']
result_dfs[2].columns = ['Course', 'Instructor_Fall']

# concat
df_instructor_courses = result_dfs[0].merge(result_dfs[1], how='outer', on='Course')
df_instructor_courses = df_instructor_courses.merge(result_dfs[2], how='outer', on='Course')


In [210]:
df

1     2         3         4     5         6         7     8  \
0     3.136000  3.29  3.038000  3.210000  3.21  2.998000  3.086000  3.00   
1     2.770000  3.27  3.120000  3.150000  3.55  3.290000  3.156667  3.11   
2     3.336667   NaN       NaN  3.336667   NaN       NaN  3.336667   NaN   
3     4.000000   NaN  3.956667  3.900000   NaN  4.000000  4.000000   NaN   
4     3.746667  4.00  3.596667  3.746667  4.00  3.626667  3.783333  4.00   
...        ...   ...       ...       ...   ...       ...       ...   ...   
4574  4.000000   NaN  3.875000  4.000000   NaN  3.875000  4.000000   NaN   
4575  3.863636   NaN  4.000000  3.863636   NaN  4.000000  3.863636   NaN   
4576  3.390000  4.00  3.800000  3.390000  4.00  3.800000  3.390000  4.00   
4577       NaN   NaN  3.880000       NaN   NaN  3.880000       NaN   NaN   
4578  4.000000   NaN  4.000000  4.000000   NaN  4.000000  4.000000   NaN   

          9        10  ...        39        40        41        42        43  \
0     3.216  3.136000  ...  2.816882  3.072566  3.234039  2.908065  2.942821   
1     3.160  3.226667  ...  3.359264  3.509813  3.229542  3.342054  3.504470   
2       NaN  3.336667  ...       NaN  3.336667       NaN       NaN  3.336667   
3     3.955  4.000000  ...  4.000000  4.000000       NaN  4.000000  4.000000   
4     3.900  3.733333  ...  3.885728  3.843286  4.000000  3.887007  3.842477   
...     ...       ...  ...       ...       ...       ...       ...       ...   
4574  3.875  4.000000  ...  4.000000  4.000000       NaN  4.000000  4.000000   
4575  4.000  3.863636  ...  3.901443  3.916746       NaN  3.898869  3.918329   
4576  3.800  3.390000  ...  3.800000  3.999999  4.000000  3.800000  3.999999   
4577  3.880       NaN  ...  3.880000       NaN       NaN  3.880000       NaN   
4578  4.000  4.000000  ...  4.000000  3.800000       NaN  4.000000  3.800000   

            44        45        46        47     Course  
0     3.218919  2.783447  3.067042  3.226656  ACCT 2101  
1     3.228847  3.342403  3.507211  3.228301  ACCT 2102  
2          NaN       NaN  3.336667       NaN    AE 1350  
3          NaN  4.000000  4.000000       NaN    AE 1355  
4     4.000000  3.883027  3.838174  4.000000    AE 1601  
...        ...       ...       ...       ...        ...  
4574       NaN  4.000000  4.000000       NaN   VIP 6602  
4575       NaN  3.899321  3.953490       NaN   VIP 6603  
4576  4.000000  3.800000  3.999999  4.000000  WOLO 1801  
4577       NaN  3.880000       NaN       NaN  WOLO 1811  
4578       NaN  4.000000  3.800000       NaN  WOLO 3420  

[4579 rows x 48 columns]

## Merge with the overall df

In [211]:
df = df.merge(df_instructor_courses, how='left', on='Course')

In [212]:
df

1     2         3         4     5         6         7     8  \
0     3.136000  3.29  3.038000  3.210000  3.21  2.998000  3.086000  3.00   
1     2.770000  3.27  3.120000  3.150000  3.55  3.290000  3.156667  3.11   
2     3.336667   NaN       NaN  3.336667   NaN       NaN  3.336667   NaN   
3     4.000000   NaN  3.956667  3.900000   NaN  4.000000  4.000000   NaN   
4     3.746667  4.00  3.596667  3.746667  4.00  3.626667  3.783333  4.00   
...        ...   ...       ...       ...   ...       ...       ...   ...   
4574  4.000000   NaN  3.875000  4.000000   NaN  3.875000  4.000000   NaN   
4575  3.863636   NaN  4.000000  3.863636   NaN  4.000000  3.863636   NaN   
4576  3.390000  4.00  3.800000  3.390000  4.00  3.800000  3.390000  4.00   
4577       NaN   NaN  3.880000       NaN   NaN  3.880000       NaN   NaN   
4578  4.000000   NaN  4.000000  4.000000   NaN  4.000000  4.000000   NaN   

          9        10  ...        42        43        44        45        46  \
0     3.216  3.136000  ...  2.908065  2.942821  3.218919  2.783447  3.067042   
1     3.160  3.226667  ...  3.342054  3.504470  3.228847  3.342403  3.507211   
2       NaN  3.336667  ...       NaN  3.336667       NaN       NaN  3.336667   
3     3.955  4.000000  ...  4.000000  4.000000       NaN  4.000000  4.000000   
4     3.900  3.733333  ...  3.887007  3.842477  4.000000  3.883027  3.838174   
...     ...       ...  ...       ...       ...       ...       ...       ...   
4574  3.875  4.000000  ...  4.000000  4.000000       NaN  4.000000  4.000000   
4575  4.000  3.863636  ...  3.898869  3.918329       NaN  3.899321  3.953490   
4576  3.800  3.390000  ...  3.800000  3.999999  4.000000  3.800000  3.999999   
4577  3.880       NaN  ...  3.880000       NaN       NaN  3.880000       NaN   
4578  4.000  4.000000  ...  4.000000  3.800000       NaN  4.000000  3.800000   

            47     Course  Instructor_Spring     Instructor_Summer  \
0     3.226656  ACCT 2101  Schneider, Arnold       Turner, Deborah   
1     3.228301  ACCT 2102       Blunck, Ryan             Kuang, Xi   
2          NaN    AE 1350                NaN                   NaN   
3          NaN    AE 1355                NaN         Johnson, Carl   
4     4.000000    AE 1601  Griendling, Kelly     Griendling, Kelly   
...        ...        ...                ...                   ...   
4574       NaN   VIP 6602                NaN        Vela, Patricio   
4575       NaN   VIP 6603                NaN          Zutty, Jason   
4576  4.000000  WOLO 1801          Sy, Samba             Sy, Samba   
4577       NaN  WOLO 1811                NaN             Sy, Samba   
4578       NaN  WOLO 3420                NaN  Ippolito, Christophe   

          Instructor_Fall  
0       Schneider, Arnold  
1               Kuang, Xi  
2     Steinfeldt, Bradley  
3           Johnson, Carl  
4         Ruffin, Stephen  
...                   ...  
4574         Zhang, Fumin  
4575         Young, Aaron  
4576            Sy, Samba  
4577                  NaN  
4578   Stepanov, Brigitte  

[4579 rows x 51 columns]

# Write output in Devanshu's desired format

Fix column names

In [213]:
df['Cred_hours'] = 3
df['Pre-req'] = ''

Get predictions only

In [214]:
df_preds = df.copy()
df_preds = df_preds.drop(columns=[1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29])

In [215]:
df_preds

30        31        32        33        34        35        36  \
0     3.032881  3.125060  3.158509  2.876693  2.975500  3.262099  2.952837   
1     3.325903  3.513665  3.219985  3.310294  3.518184  3.220285  3.356868   
2          NaN  3.336667       NaN       NaN  3.336667       NaN       NaN   
3     4.000000  4.000000       NaN  4.000000  4.000000       NaN  4.000000   
4     3.883828  3.843719  4.000000  3.895058  3.852294  4.000000  3.878028   
...        ...       ...       ...       ...       ...       ...       ...   
4574  4.000000  4.000000       NaN  4.000000  4.000000       NaN  4.000000   
4575  3.891370  3.898318       NaN  3.905729  3.917707       NaN  3.895533   
4576  3.800000  3.999999  4.000000  3.800000  3.999999  4.000000  3.800000   
4577  3.880000       NaN       NaN  3.880000       NaN       NaN  3.880000   
4578  4.000000  3.800000       NaN  4.000000  3.800000       NaN  4.000000   

            37        38        39  ...        44        45        46  \
0     2.985407  3.205621  2.816882  ...  3.218919  2.783447  3.067042   
1     3.505319  3.227541  3.359264  ...  3.228847  3.342403  3.507211   
2     3.336667       NaN       NaN  ...       NaN       NaN  3.336667   
3     4.000000       NaN  4.000000  ...       NaN  4.000000  4.000000   
4     3.830766  4.000000  3.885728  ...  4.000000  3.883027  3.838174   
...        ...       ...       ...  ...       ...       ...       ...   
4574  4.000000       NaN  4.000000  ...       NaN  4.000000  4.000000   
4575  3.967215       NaN  3.901443  ...       NaN  3.899321  3.953490   
4576  3.999999  4.000000  3.800000  ...  4.000000  3.800000  3.999999   
4577       NaN       NaN  3.880000  ...       NaN  3.880000       NaN   
4578  3.800000       NaN  4.000000  ...       NaN  4.000000  3.800000   

            47     Course  Instructor_Spring     Instructor_Summer  \
0     3.226656  ACCT 2101  Schneider, Arnold       Turner, Deborah   
1     3.228301  ACCT 2102       Blunck, Ryan             Kuang, Xi   
2          NaN    AE 1350                NaN                   NaN   
3          NaN    AE 1355                NaN         Johnson, Carl   
4     4.000000    AE 1601  Griendling, Kelly     Griendling, Kelly   
...        ...        ...                ...                   ...   
4574       NaN   VIP 6602                NaN        Vela, Patricio   
4575       NaN   VIP 6603                NaN          Zutty, Jason   
4576  4.000000  WOLO 1801          Sy, Samba             Sy, Samba   
4577       NaN  WOLO 1811                NaN             Sy, Samba   
4578       NaN  WOLO 3420                NaN  Ippolito, Christophe   

          Instructor_Fall Cred_hours Pre-req  
0       Schneider, Arnold          3          
1               Kuang, Xi          3          
2     Steinfeldt, Bradley          3          
3           Johnson, Carl          3          
4         Ruffin, Stephen          3          
...                   ...        ...     ...  
4574         Zhang, Fumin          3          
4575         Young, Aaron          3          
4576            Sy, Samba          3          
4577                  NaN          3          
4578   Stepanov, Brigitte          3          

[4579 rows x 24 columns]

In [216]:
df_preds.columns = ['Pred_1', 'Pred_2', 'Pred_3', 'Pred_4', 'Pred_5', 'Pred_6', 'Pred_7', 'Pred_8', 'Pred_9', 'Pred_10', 'Pred_11', 'Pred_12', 'Pred_13', 'Pred_14', 'Pred_15', 'Pred_16', 'Pred_17', 'Pred_18', 'Course', 'Instructor_Spring','Instructor_Summer','Instructor_Fall', 'Cred_hours', 'Pre-req']

Add instructor columns

In [217]:
df_preds['Instructor_1'] = df_preds['Instructor_Spring']
df_preds['Instructor_4'] = df_preds['Instructor_Spring']
df_preds['Instructor_7'] = df_preds['Instructor_Spring']
df_preds['Instructor_10'] = df_preds['Instructor_Spring']
df_preds['Instructor_13'] = df_preds['Instructor_Spring']
df_preds['Instructor_16'] = df_preds['Instructor_Spring']

df_preds['Instructor_2'] = df_preds['Instructor_Summer']
df_preds['Instructor_5'] = df_preds['Instructor_Summer']
df_preds['Instructor_8'] = df_preds['Instructor_Summer']
df_preds['Instructor_11'] = df_preds['Instructor_Summer']
df_preds['Instructor_14'] = df_preds['Instructor_Summer']
df_preds['Instructor_17'] = df_preds['Instructor_Summer']

df_preds['Instructor_3'] = df_preds['Instructor_Fall']
df_preds['Instructor_6'] = df_preds['Instructor_Fall']
df_preds['Instructor_9'] = df_preds['Instructor_Fall']
df_preds['Instructor_12'] = df_preds['Instructor_Fall']
df_preds['Instructor_15'] = df_preds['Instructor_Fall']
df_preds['Instructor_18'] = df_preds['Instructor_Fall']


In [218]:
df_preds

Pred_1    Pred_2    Pred_3    Pred_4    Pred_5    Pred_6    Pred_7  \
0     3.032881  3.125060  3.158509  2.876693  2.975500  3.262099  2.952837   
1     3.325903  3.513665  3.219985  3.310294  3.518184  3.220285  3.356868   
2          NaN  3.336667       NaN       NaN  3.336667       NaN       NaN   
3     4.000000  4.000000       NaN  4.000000  4.000000       NaN  4.000000   
4     3.883828  3.843719  4.000000  3.895058  3.852294  4.000000  3.878028   
...        ...       ...       ...       ...       ...       ...       ...   
4574  4.000000  4.000000       NaN  4.000000  4.000000       NaN  4.000000   
4575  3.891370  3.898318       NaN  3.905729  3.917707       NaN  3.895533   
4576  3.800000  3.999999  4.000000  3.800000  3.999999  4.000000  3.800000   
4577  3.880000       NaN       NaN  3.880000       NaN       NaN  3.880000   
4578  4.000000  3.800000       NaN  4.000000  3.800000       NaN  4.000000   

        Pred_8    Pred_9   Pred_10  ...          Instructor_8  \
0     2.985407  3.205621  2.816882  ...       Turner, Deborah   
1     3.505319  3.227541  3.359264  ...             Kuang, Xi   
2     3.336667       NaN       NaN  ...                   NaN   
3     4.000000       NaN  4.000000  ...         Johnson, Carl   
4     3.830766  4.000000  3.885728  ...     Griendling, Kelly   
...        ...       ...       ...  ...                   ...   
4574  4.000000       NaN  4.000000  ...        Vela, Patricio   
4575  3.967215       NaN  3.901443  ...          Zutty, Jason   
4576  3.999999  4.000000  3.800000  ...             Sy, Samba   
4577       NaN       NaN  3.880000  ...             Sy, Samba   
4578  3.800000       NaN  4.000000  ...  Ippolito, Christophe   

             Instructor_11         Instructor_14         Instructor_17  \
0          Turner, Deborah       Turner, Deborah       Turner, Deborah   
1                Kuang, Xi             Kuang, Xi             Kuang, Xi   
2                      NaN                   NaN                   NaN   
3            Johnson, Carl         Johnson, Carl         Johnson, Carl   
4        Griendling, Kelly     Griendling, Kelly     Griendling, Kelly   
...                    ...                   ...                   ...   
4574        Vela, Patricio        Vela, Patricio        Vela, Patricio   
4575          Zutty, Jason          Zutty, Jason          Zutty, Jason   
4576             Sy, Samba             Sy, Samba             Sy, Samba   
4577             Sy, Samba             Sy, Samba             Sy, Samba   
4578  Ippolito, Christophe  Ippolito, Christophe  Ippolito, Christophe   

             Instructor_3         Instructor_6         Instructor_9  \
0       Schneider, Arnold    Schneider, Arnold    Schneider, Arnold   
1               Kuang, Xi            Kuang, Xi            Kuang, Xi   
2     Steinfeldt, Bradley  Steinfeldt, Bradley  Steinfeldt, Bradley   
3           Johnson, Carl        Johnson, Carl        Johnson, Carl   
4         Ruffin, Stephen      Ruffin, Stephen      Ruffin, Stephen   
...                   ...                  ...                  ...   
4574         Zhang, Fumin         Zhang, Fumin         Zhang, Fumin   
4575         Young, Aaron         Young, Aaron         Young, Aaron   
4576            Sy, Samba            Sy, Samba            Sy, Samba   
4577                  NaN                  NaN                  NaN   
4578   Stepanov, Brigitte   Stepanov, Brigitte   Stepanov, Brigitte   

            Instructor_12        Instructor_15        Instructor_18  
0       Schneider, Arnold    Schneider, Arnold    Schneider, Arnold  
1               Kuang, Xi            Kuang, Xi            Kuang, Xi  
2     Steinfeldt, Bradley  Steinfeldt, Bradley  Steinfeldt, Bradley  
3           Johnson, Carl        Johnson, Carl        Johnson, Carl  
4         Ruffin, Stephen      Ruffin, Stephen      Ruffin, Stephen  
...                   ...                  ...                  ...  
4574         Zhang, Fumin         Zhang, Fumin         Zha

Drop other instructor columns

In [219]:
df_preds.drop(columns=['Instructor_Spring','Instructor_Summer','Instructor_Fall'], inplace=True)

Reorder

In [220]:
df_preds = df_preds[['Course', 'Cred_hours', 'Pre-req', 'Pred_1', 'Instructor_1', 'Pred_2', 'Instructor_2', 'Pred_3', 'Instructor_3', 'Pred_4', 'Instructor_4', 'Pred_5', 'Instructor_5', 'Pred_6', 'Instructor_6', 'Pred_7', 'Instructor_7', 'Pred_8', 'Instructor_8', 'Pred_9', 'Instructor_9', 'Pred_10', 'Instructor_10', 'Pred_11', 'Instructor_11', 'Pred_12', 'Instructor_12', 'Pred_13', 'Instructor_13', 'Pred_14', 'Instructor_14', 'Pred_15', 'Instructor_15', 'Pred_16', 'Instructor_16', 'Pred_17', 'Instructor_17', 'Pred_18', 'Instructor_18']]

In [221]:
df_preds

Course  Cred_hours Pre-req    Pred_1       Instructor_1    Pred_2  \
0     ACCT 2101           3          3.032881  Schneider, Arnold  3.125060   
1     ACCT 2102           3          3.325903       Blunck, Ryan  3.513665   
2       AE 1350           3               NaN                NaN  3.336667   
3       AE 1355           3          4.000000                NaN  4.000000   
4       AE 1601           3          3.883828  Griendling, Kelly  3.843719   
...         ...         ...     ...       ...                ...       ...   
4574   VIP 6602           3          4.000000                NaN  4.000000   
4575   VIP 6603           3          3.891370                NaN  3.898318   
4576  WOLO 1801           3          3.800000          Sy, Samba  3.999999   
4577  WOLO 1811           3          3.880000                NaN       NaN   
4578  WOLO 3420           3          4.000000                NaN  3.800000   

              Instructor_2    Pred_3         Instructor_3    Pred_4  ...  \
0          Turner, Deborah  3.158509    Schneider, Arnold  2.876693  ...   
1                Kuang, Xi  3.219985            Kuang, Xi  3.310294  ...   
2                      NaN       NaN  Steinfeldt, Bradley       NaN  ...   
3            Johnson, Carl       NaN        Johnson, Carl  4.000000  ...   
4        Griendling, Kelly  4.000000      Ruffin, Stephen  3.895058  ...   
...                    ...       ...                  ...       ...  ...   
4574        Vela, Patricio       NaN         Zhang, Fumin  4.000000  ...   
4575          Zutty, Jason       NaN         Young, Aaron  3.905729  ...   
4576             Sy, Samba  4.000000            Sy, Samba  3.800000  ...   
4577             Sy, Samba       NaN                  NaN  3.880000  ...   
4578  Ippolito, Christophe       NaN   Stepanov, Brigitte  4.000000  ...   

       Pred_14         Instructor_14   Pred_15        Instructor_15   Pred_16  \
0     2.942821       Turner, Deborah  3.218919    Schneider, Arnold  2.783447   
1     3.504470             Kuang, Xi  3.228847            Kuang, Xi  3.342403   
2     3.336667                   NaN       NaN  Steinfeldt, Bradley       NaN   
3     4.000000         Johnson, Carl       NaN        Johnson, Carl  4.000000   
4     3.842477     Griendling, Kelly  4.000000      Ruffin, Stephen  3.883027   
...        ...                   ...       ...                  ...       ...   
4574  4.000000        Vela, Patricio       NaN         Zhang, Fumin  4.000000   
4575  3.918329          Zutty, Jason       NaN         Young, Aaron  3.899321   
4576  3.999999             Sy, Samba  4.000000            Sy, Samba  3.800000   
4577       NaN             Sy, Samba       NaN                  NaN  3.880000   
4578  3.800000  Ippolito, Christophe       NaN   Stepanov, Brigitte  4.000000   

          Instructor_16   Pred_17         Instructor_17   Pred_18  \
0     Schneider, Arnold  3.067042       Turner, Deborah  3.226656   
1          Blunck, Ryan  3.507211             Kuang, Xi  3.228301   
2                   NaN  3.336667                   NaN       NaN   
3                   NaN  4.000000         Johnson, Carl       NaN   
4     Griendling, Kelly  3.838174     Griendling, Kelly  4.000000   
...                 ...       ...                   ...       ...   
4574                NaN  4.000000        Vela, Patricio       NaN   
4575                NaN  3.953490          Zutty, Jason       NaN   
4576          Sy, Samba  3.999999             Sy, Samba  4.000000   
4577                NaN       NaN             Sy, Samba       NaN   
4578                NaN  3.800000  Ippolito, Christophe       NaN   

            Instructor_18  
0       Schneider, Arnold  
1               Kuang, Xi  
2     Steinfeldt, Bradley  
3           Johnson, Carl  
4         Ruffin, Stephen  
...                   ...  
4574         Zhang, Fumin  
4575         Young, Aaron  
4576            Sy, Samba  
4577                  NaN  
4578   Stepanov, Brigitte  

[4579 rows x 39 colu

Save with Nans

In [229]:
df_preds.to_csv("all_predictions_with_nans.csv", index=False)

In [230]:
df_preds_backup = df_preds.copy()

Interpolate to get rid of nans

In [240]:
# Step 1: Separate numeric and non-numeric columns, excluding 'Cred_hours'
numeric_cols = df_preds.select_dtypes(include='number').drop('Cred_hours', axis=1)
non_numeric_cols = df_preds.select_dtypes(exclude='number')

# Store 'Cred_hours' column
cred_hours_column = df_preds['Cred_hours']

# Step 2: Perform linear interpolation on numeric columns
interpolated_numeric_cols = numeric_cols.interpolate(method='linear', axis=0)

# Step 3: Apply forward fill and backward fill
interpolated_numeric_cols = interpolated_numeric_cols.ffill(axis=0).bfill(axis=0)

# Step 4: Combine interpolated numeric columns with non-numeric columns and 'Cred_hours'
df_filled = pd.concat([interpolated_numeric_cols, non_numeric_cols, cred_hours_column], axis=1)


In [241]:
df_filled

Pred_1    Pred_2    Pred_3    Pred_4    Pred_5    Pred_6    Pred_7  \
0     3.032881  3.125060  3.158509  2.876693  2.975500  3.262099  2.952837   
1     3.325903  3.513665  3.219985  3.310294  3.518184  3.220285  3.356868   
2     3.662951  3.336667  3.479990  3.655147  3.336667  3.480190  3.678434   
3     4.000000  4.000000  3.739995  4.000000  4.000000  3.740095  4.000000   
4     3.883828  3.843719  4.000000  3.895058  3.852294  4.000000  3.878028   
...        ...       ...       ...       ...       ...       ...       ...   
4574  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000  4.000000   
4575  3.891370  3.898318  4.000000  3.905729  3.917707  4.000000  3.895533   
4576  3.800000  3.999999  4.000000  3.800000  3.999999  4.000000  3.800000   
4577  3.880000  3.900000  4.000000  3.880000  3.900000  4.000000  3.880000   
4578  4.000000  3.800000  4.000000  4.000000  3.800000  4.000000  4.000000   

        Pred_8    Pred_9   Pred_10  ...      Instructor_10  \
0     2.985407  3.205621  2.816882  ...  Schneider, Arnold   
1     3.505319  3.227541  3.359264  ...       Blunck, Ryan   
2     3.336667  3.485027  3.679632  ...                NaN   
3     4.000000  3.742514  4.000000  ...                NaN   
4     3.830766  4.000000  3.885728  ...  Griendling, Kelly   
...        ...       ...       ...  ...                ...   
4574  4.000000  4.000000  4.000000  ...                NaN   
4575  3.967215  4.000000  3.901443  ...                NaN   
4576  3.999999  4.000000  3.800000  ...          Sy, Samba   
4577  3.900000  4.000000  3.880000  ...                NaN   
4578  3.800000  4.000000  4.000000  ...                NaN   

             Instructor_11        Instructor_12      Instructor_13  \
0          Turner, Deborah    Schneider, Arnold  Schneider, Arnold   
1                Kuang, Xi            Kuang, Xi       Blunck, Ryan   
2                      NaN  Steinfeldt, Bradley                NaN   
3            Johnson, Carl        Johnson, Carl                NaN   
4        Griendling, Kelly      Ruffin, Stephen  Griendling, Kelly   
...                    ...                  ...                ...   
4574        Vela, Patricio         Zhang, Fumin                NaN   
4575          Zutty, Jason         Young, Aaron                NaN   
4576             Sy, Samba            Sy, Samba          Sy, Samba   
4577             Sy, Samba                  NaN                NaN   
4578  Ippolito, Christophe   Stepanov, Brigitte                NaN   

             Instructor_14        Instructor_15      Instructor_16  \
0          Turner, Deborah    Schneider, Arnold  Schneider, Arnold   
1                Kuang, Xi            Kuang, Xi       Blunck, Ryan   
2                      NaN  Steinfeldt, Bradley                NaN   
3            Johnson, Carl        Johnson, Carl                NaN   
4        Griendling, Kelly      Ruffin, Stephen  Griendling, Kelly   
...                    ...                  ...                ...   
4574        Vela, Patricio         Zhang, Fumin                NaN   
4575          Zutty, Jason         Young, Aaron                NaN   
4576             Sy, Samba            Sy, Samba          Sy, Samba   
4577             Sy, Samba                  NaN                NaN   
4578  Ippolito, Christophe   Stepanov, Brigitte                NaN   

             Instructor_17        Instructor_18 Cred_hours  
0          Turner, Deborah    Schneider, Arnold          3  
1                Kuang, Xi            Kuang, Xi          3  
2                      NaN  Steinfeldt, Bradley          3  
3            Johnson, Carl        Johnson, Carl          3  
4        Griendling, Kelly      Ruffin, Stephen          3  
...                    ...                  ...        ...  
4574        Vela, Patricio         Zhang, Fumin          3  
4575          Zutty, Jason         Young, Aaron          3  
4576             Sy, Samba            Sy, Samba          3  
4577             Sy, Samba        

Aagain reorder columns

In [242]:
df_preds = df_filled[['Course', 'Cred_hours', 'Pre-req', 'Pred_1', 'Instructor_1', 'Pred_2', 'Instructor_2', 'Pred_3', 'Instructor_3', 'Pred_4', 'Instructor_4', 'Pred_5', 'Instructor_5', 'Pred_6', 'Instructor_6', 'Pred_7', 'Instructor_7', 'Pred_8', 'Instructor_8', 'Pred_9', 'Instructor_9', 'Pred_10', 'Instructor_10', 'Pred_11', 'Instructor_11', 'Pred_12', 'Instructor_12', 'Pred_13', 'Instructor_13', 'Pred_14', 'Instructor_14', 'Pred_15', 'Instructor_15', 'Pred_16', 'Instructor_16', 'Pred_17', 'Instructor_17', 'Pred_18', 'Instructor_18']]

In [248]:
df_preds.fillna('Unknown', inplace=True)

In [249]:
df_filled.to_csv("all_predictions_with_nonans.csv", index=False)